In [1]:
import veroviz as vrv
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import folium
from ipyleaflet import Map, Marker, Polyline
import geopandas as gpd
from shapely.geometry import Point, LineString, Polygon
import json
import requests
import os
import polyline
import geopy.distance

In [2]:
# Setting up matplotlib to display inline in Jupyter notebooks
%matplotlib inline

In [3]:
def get_osrm_route(start, end, server='http://router.project-osrm.org'):
    coords = f"{start[1]},{start[0]};{end[1]},{end[0]}"
    url = f"{server}/route/v1/driving/{coords}?overview=full"
    try:
        response = requests.get(url).json()
        if response['code'] == 'Ok':
            encoded_polyline = response['routes'][0]['geometry']
            route = polyline.decode(encoded_polyline)
            return [{'coordinates': {'lat': pt[0], 'lng': pt[1]}} for pt in route], None
        else:
            # Return a more descriptive error message
            return None, f"Error from OSRM: {response.get('message', 'No specific error message')}"
    except Exception as e:
        # Return the exception message itself if an exception occurs
        return None, f"Exception in getting OSRM route: {str(e)}"

In [4]:
def load_json_files(directory):
    # Map of route IDs to city names
    route_to_city = {
        "0ba52062-f98a-4750-a6ef-0a72ff35202e": "Chicago",
        "69233ee9-1ac4-4d89-b322-94fb13df54a3": "LA",
        "02f91cfa-3839-4e55-91a0-ab19c3e77683": "Seattle",
        "ed9dd222-9ce7-47f3-8cd9-d2a5d2b6a493": "Austin",
        "e9939a49-8f0d-439f-80d9-1840dc1376ca": "Boston"
    }

    data_objects = {}
    for filename in os.listdir(directory):
        if filename.endswith('.json'):  # Ensure it's a JSON file
            # Extract the route ID from the filename
            route_id = filename.split('_')[1]
            if route_id in route_to_city:
                file_path = os.path.join(directory, filename)
                with open(file_path, 'r') as file:
                    file_data = json.load(file)
                    city_name = route_to_city[route_id]
                    # Combine all events under each city name
                    if city_name not in data_objects:
                        data_objects[city_name] = []
                    data_objects[city_name].extend(file_data)  # Append events directly

    return data_objects

# Usage example with paths to directories
vehicle_only_events_directory_path = '../algorithm/amazon_vehicle_events'
vehicle_only_paths_directory_path = '../algorithm/amazon_vehicle_paths'

vehicle_only_events = load_json_files(vehicle_only_events_directory_path)
vehicle_only_paths = load_json_files(vehicle_only_paths_directory_path)


In [5]:
for key, value in vehicle_only_paths.items():
    print({key:value})

{'Boston': [{'id': 1, 'stop': 'SW', 'coordinates': {'lat': 42.139891, 'lng': -71.494346}}, {'id': 2, 'stop': 'DO', 'coordinates': {'lat': 42.207436, 'lng': -71.684275}}, {'id': 3, 'stop': 'SQ', 'coordinates': {'lat': 42.208183, 'lng': -71.683617}}, {'id': 4, 'stop': 'IA', 'coordinates': {'lat': 42.209057, 'lng': -71.682809}}, {'id': 5, 'stop': 'KG', 'coordinates': {'lat': 42.209494, 'lng': -71.682438}}, {'id': 6, 'stop': 'IB', 'coordinates': {'lat': 42.210583, 'lng': -71.682959}}, {'id': 7, 'stop': 'SS', 'coordinates': {'lat': 42.210652, 'lng': -71.681458}}, {'id': 8, 'stop': 'ZH', 'coordinates': {'lat': 42.211819, 'lng': -71.680066}}, {'id': 9, 'stop': 'XW', 'coordinates': {'lat': 42.212, 'lng': -71.677426}}, {'id': 10, 'stop': 'GC', 'coordinates': {'lat': 42.212232, 'lng': -71.675846}}, {'id': 11, 'stop': 'SF', 'coordinates': {'lat': 42.218855, 'lng': -71.677317}}, {'id': 12, 'stop': 'FR', 'coordinates': {'lat': 42.206324, 'lng': -71.677589}}, {'id': 13, 'stop': 'WR', 'coordinates': 

In [6]:
vehicle_only_events['Chicago']

[{'id': 1,
  'event_type': 'DEPART',
  'stop_id': 'VE',
  'time': 0,
  'coordinates': {'lat': 42.031368, 'lng': -87.776596}},
 {'id': 2,
  'event_type': 'ARRIVE',
  'stop_id': 'TG',
  'time': 644.2,
  'coordinates': {'lat': 42.040283, 'lng': -87.732541}},
 {'id': 3,
  'event_type': 'SERVICE_START',
  'stop_id': 'TG',
  'time': 644.2,
  'coordinates': {'lat': 42.040283, 'lng': -87.732541}},
 {'id': 4,
  'event_type': 'SERVICE_END',
  'stop_id': 'TG',
  'time': 737.0,
  'coordinates': {'lat': 42.040283, 'lng': -87.732541}},
 {'id': 5,
  'event_type': 'DEPART',
  'stop_id': 'TG',
  'time': 737.0,
  'coordinates': {'lat': 42.040283, 'lng': -87.732541}},
 {'id': 6,
  'event_type': 'ARRIVE',
  'stop_id': 'GP',
  'time': 784.7,
  'coordinates': {'lat': 42.040451, 'lng': -87.73142}},
 {'id': 7,
  'event_type': 'SERVICE_START',
  'stop_id': 'GP',
  'time': 784.7,
  'coordinates': {'lat': 42.040451, 'lng': -87.73142}},
 {'id': 8,
  'event_type': 'SERVICE_END',
  'stop_id': 'GP',
  'time': 831.7,

In [7]:
def process_single_city_events(events):
    """Process the event data for a single city and return a DataFrame with structured data."""
    # Normalize data and create DataFrame for each event list independently
    df = pd.DataFrame(events)

    # Calculate and handle each attribute, ensuring all entries are processed independently
    processed_df = pd.DataFrame({
        'id': df['id'],
        'lat': df['coordinates'].apply(lambda x: x['lat']),
        'lon': df['coordinates'].apply(lambda x: x['lng']),
        'elevMeters': 0,
        'objectID': df['id'],
        'startTimeSec': df['time'],
        'nodeName': df.apply(lambda x: f"Node {x['id']}", axis=1),
        'nodeType': 'Waypoint',
        'popupText': df.apply(lambda x: f"{x['id']} Event: {x['event_type']}<br>Time: {x['time']}", axis=1),
        'leafletIconPrefix': 'fa',
        'leafletIconType': df['id'].apply(lambda x: 'flag' if x % 2 == 0 else 'circle'),
        'leafletColor': df['id'].apply(lambda x: 'green' if x % 2 == 0 else 'blue'),
        'leafletIconText': df['id'].apply(str),
        'cesiumIconType': 'pin',
        'cesiumColor': df['id'].apply(lambda x: 'red' if x % 2 == 0 else 'yellow'),
        'cesiumIconText': df['id'].apply(str),
        'altMeters': 0,
        'stopID': df['stop_id']
    })

    return processed_df

# Dictionary to hold processed DataFrames for each city
vehicle_only_events_dataframes = {}

# Loop over each city and its associated events data
for city, events in vehicle_only_events.items():
    vehicle_only_events_dataframes[city] = process_single_city_events(events)


In [8]:
vehicle_only_nodes = vehicle_only_events_dataframes

In [9]:
mp = {}
for city, df in vehicle_only_nodes.items():
    mp[city] = {}
    for i, row in df.iterrows():
        mp[city][row['stopID']] = i

In [10]:
vehicle_props = {
    'Austin': {'modelFile': 'truck.glb', 'color': 'red'},
    'Chicago': {'modelFile': 'truck.glb', 'color': 'blue'},
    'Seattle': {'modelFile': 'truck.glb', 'color': 'green'},
    'Boston': {'modelFile': 'truck.glb', 'color': 'yellow'},
    'LA': {'modelFile': 'truck.glb', 'color': 'purple'}
}

def create_vehicle_only_rows(odID, objectID, vehicle_props, route, times):
    if not route:
        print(f"Empty route received for {objectID}.")
        return []

    rows = []
    for i in range(len(route) - 1):
        start_point = route[i]['coordinates']
        end_point = route[i+1]['coordinates']
        row = {
            'odID': odID + i,
            'objectID': objectID,
            'modelFile': vehicle_props[objectID]['modelFile'],
            'startLat': start_point['lat'],
            'startLon': start_point['lng'],
            'endLat': end_point['lat'],
            'endLon': end_point['lng'],
            'startElevMeters': 0,  # Example default value
            'endElevMeters': 0,
            'startAltMeters': 100 if objectID == 'drone' else 0,  # Example customization for drones
            'endAltMeters': 100 if objectID == 'drone' else 0,
            'startTimeSec': times[i],
            'endTimeSec': times[i+1],
            'leafletColor': vehicle_props[objectID]['color'],
            'leafletWeight': 5,
            'leafletStyle': 'solid',
            'leafletOpacity': 0.8,
            'leafletCurveType': 'straight',
            'leafletCurvature': 0,
            'arcCurveType': 'straight',
            'useArrows': True,
            'cesiumColor': vehicle_props[objectID]['color'],
            'cesiumWeight': 5,
            'cesiumStyle': 'solid',
            'cesiumOpacity': 0.8,
            'popupText': f'Route segment {i+1} for {objectID}'
        }
        rows.append(row)

    return rows


def process_vehicle_paths(vehicle_paths, vehicle_props):
    all_rows = []
    odID = 1

    for objectID, path in vehicle_paths.items():
        print(f"Processing path for {objectID} with {len(path)} stops.")
        for i in range(len(path) - 1):
            start = path[i]['coordinates']
            end = path[i+1]['coordinates']
            route, error = get_osrm_route((start['lat'], start['lng']), (end['lat'], end['lng']))
            if error:
                print(f"Error processing segment {i+1} in {objectID}: {error}")
                continue  # Skip this segment due to error

            # interpolate times
            times = []
            start_time = vehicle_only_nodes[objectID].loc[mp[objectID][path[i]['stop']], 'startTimeSec']
            end_time = vehicle_only_nodes[objectID].loc[mp[objectID][path[i+1]['stop']], 'startTimeSec']
            if route:
                tot = 0
                for i in range(len(route) - 1):
                    di = geopy.distance.distance((start['lat'], start['lng']), (end['lat'], end['lng'])).km
                    tot += di
                times.append(start_time)
                for i in range(len(route) - 1):
                    di = geopy.distance.distance((start['lat'], start['lng']), (end['lat'], end['lng'])).km
                    times.append(times[-1] if tot == 0 else times[-1] + (end_time - start_time) * di / tot)

            rows = create_vehicle_only_rows(odID, objectID, vehicle_props, route, times)
            all_rows.extend(rows)
            odID += len(rows)

    return all_rows


In [11]:
def validate_route_data(routes):
    for i, route in enumerate(routes):
        if 'stop' not in route or 'coordinates' not in route or 'id' not in route:
            print(f"Data missing in route at index {i}: {route}")
        if 'lat' not in route['coordinates'] or 'lng' not in route['coordinates']:
            print(f"Coordinate data missing in route at index {i}: {route}")

# Example use:
validate_route_data(vehicle_only_paths['Boston'])

In [12]:
vehicle_only_rows = process_vehicle_paths(vehicle_only_paths, vehicle_props)

Processing path for Boston with 167 stops.
Processing path for Chicago with 204 stops.
Processing path for LA with 139 stops.
Processing path for Seattle with 84 stops.
Processing path for Austin with 167 stops.


In [13]:
vehicle_only_assignments = vehicle_only_rows

In [14]:
for key, value in vehicle_only_paths.items():
    print(len(value))

167
204
139
84
167


In [15]:
len(vehicle_only_rows)

15068

In [16]:
vehicle_only_assignments

[{'odID': 1,
  'objectID': 'Boston',
  'modelFile': 'truck.glb',
  'startLat': 42.13989,
  'startLon': -71.4943,
  'endLat': 42.14031,
  'endLon': -71.49422,
  'startElevMeters': 0,
  'endElevMeters': 0,
  'startAltMeters': 0,
  'endAltMeters': 0,
  'startTimeSec': 24930.399999999994,
  'endTimeSec': 24911.573887973635,
  'leafletColor': 'yellow',
  'leafletWeight': 5,
  'leafletStyle': 'solid',
  'leafletOpacity': 0.8,
  'leafletCurveType': 'straight',
  'leafletCurvature': 0,
  'arcCurveType': 'straight',
  'useArrows': True,
  'cesiumColor': 'yellow',
  'cesiumWeight': 5,
  'cesiumStyle': 'solid',
  'cesiumOpacity': 0.8,
  'popupText': 'Route segment 1 for Boston'},
 {'odID': 2,
  'objectID': 'Boston',
  'modelFile': 'truck.glb',
  'startLat': 42.14031,
  'startLon': -71.49422,
  'endLat': 42.14044,
  'endLon': -71.49443,
  'startElevMeters': 0,
  'endElevMeters': 0,
  'startAltMeters': 0,
  'endAltMeters': 0,
  'startTimeSec': 24911.573887973635,
  'endTimeSec': 24892.747775947275,

In [17]:
vehicle_naive_events_directory_path = '../algorithm/naive_vehicle_events'
vehicle_naive_paths_directory_path = '../algorithm/naive_vehicle_paths'
drone_naive_events_directory_path = '../algorithm/naive_drone_events'
drone_naive_paths_directory_path = '../algorithm/naive_drone_paths'

def load_json_files(directory):
    data_objects = {}
    for filename in os.listdir(directory):
        if filename.endswith('.json'):  # Ensure it's a JSON file
            file_path = os.path.join(directory, filename)
            with open(file_path, 'r') as file:
                data_objects[filename] = json.load(file)
    return data_objects

vehicle_naive_events = load_json_files(vehicle_naive_events_directory_path)
vehicle_naive_paths = load_json_files(vehicle_naive_paths_directory_path)
drone_naive_events = load_json_files(drone_naive_events_directory_path)
drone_naive_paths = load_json_files(drone_naive_paths_directory_path)

In [18]:
vehicle_optimize_events_directory_path = '../algorithm/optimized_vehicle_events'
vehicle_optimize_paths_directory_path = '../algorithm/optimized_vehicle_paths'
drone_optimize_events_directory_path = '../algorithm/optimized_drone_events'
drone_optimize_paths_directory_path = '../algorithm/optimized_drone_paths'

def load_json_files(directory):
    data_objects = {}
    for filename in os.listdir(directory):
        if filename.endswith('.json'):  # Ensure it's a JSON file
            file_path = os.path.join(directory, filename)
            with open(file_path, 'r') as file:
                data_objects[filename] = json.load(file)
    return data_objects

vehicle_optimize_events = load_json_files(vehicle_optimize_events_directory_path)
vehicle_optimize_paths = load_json_files(vehicle_optimize_paths_directory_path)
drone_optimize_events = load_json_files(drone_optimize_events_directory_path)
drone_optimize_paths = load_json_files(drone_optimize_paths_directory_path)

In [19]:
 #Initialize a new DataFrame for storing nodes using VeRoViz's initDataframe function
newNodes = vrv.initDataframe('Nodes')
# Initialize a new DataFrame for storing arcs using VeRoViz's initDataframe function
newArcs = vrv.initDataframe('Arcs')
#newArcs
newNodes

Empty DataFrame
Columns: [id, lat, lon, altMeters, nodeName, nodeType, popupText, leafletIconPrefix, leafletIconType, leafletColor, leafletIconText, cesiumIconType, cesiumColor, cesiumIconText, elevMeters]
Index: []

In [20]:
# Dictionary to store 3D model files and color properties for different vehicle types
vehicleProperties = {
    'drone': {
        'modelFile': 'veroviz/models/drone.gltf',  # Path to the 3D model file for drones
        'color': 'red'                             # Display color for drone models in visualizations
    },
    'truck': {
        'modelFile': 'veroviz/models/ub_truck.gltf',  # Path to the 3D model file for trucks
        'color': 'blue'                               # Display color for truck models in visualizations
    }
}

In [28]:
nodes_df = pd.DataFrame()
for key, value in vehicle_only_nodes.items():
    nodes_df = nodes_df.append(value)

/tmp/ipykernel_48971/1684653785.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  nodes_df = nodes_df.append(value)
/tmp/ipykernel_48971/1684653785.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  nodes_df = nodes_df.append(value)
/tmp/ipykernel_48971/1684653785.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  nodes_df = nodes_df.append(value)


In [29]:
nodes_df

id        lat        lon  elevMeters  objectID  startTimeSec  nodeName  \
0      1  42.139891 -71.494346           0         1           0.0    Node 1   
1      2  42.207436 -71.684275           0         2        2013.0    Node 2   
2      3  42.207436 -71.684275           0         3        2013.0    Node 3   
3      4  42.207436 -71.684275           0         4        2075.5    Node 4   
4      5  42.207436 -71.684275           0         5        2075.5    Node 5   
..   ...        ...        ...         ...       ...           ...       ...   
657  658  30.207181 -97.868400           0       658       20446.5  Node 658   
658  659  30.207181 -97.868400           0       659       20446.5  Node 659   
659  660  30.207181 -97.868400           0       660       20633.5  Node 660   
660  661  30.207181 -97.868400           0       661       20633.5  Node 661   
661  662  30.445236 -97.709418           0       662       22269.3  Node 662   

     nodeType                                  popupText leafletIconPrefix  \
0    Waypoint               1 Event: DEPART<br>Time: 0.0                fa   
1    Waypoint            2 Event: ARRIVE<br>Time: 2013.0                fa   
2    Waypoint     3 Event: SERVICE_START<br>Time: 2013.0                fa   
3    Waypoint       4 Event: SERVICE_END<br>Time: 2075.5                fa   
4    Waypoint            5 Event: DEPART<br>Time: 2075.5                fa   
..        ...                                        ...               ...   
657  Waypoint         658 Event: ARRIVE<br>Time: 20446.5                fa   
658  Waypoint  659 Event: SERVICE_START<br>Time: 20446.5                fa   
659  Waypoint    660 Event: SERVICE_END<br>Time: 20633.5                fa   
660  Waypoint         661 Event: DEPART<br>Time: 20633.5                fa   
661  Waypoint         662 Event: ARRIVE<br>Time: 22269.3                fa   

    leafletIconType leafletColor leafletIconText cesiumIconType cesiumColor  \
0            circle         blue               1            pin      yellow   
1              flag        green               2            pin         red   
2            circle         blue               3            pin      yellow   
3              flag        green               4            pin         red   
4            circle         blue               5            pin      yellow   
..              ...          ...             ...            ...         ...   
657            flag        green             658            pin         red   
658          circle         blue             659            pin      yellow   
659            flag        green             660            pin         red   
660          circle         blue             661            pin      yellow   
661            flag        green             662            pin         red   

    cesiumIconText  altMeters stopID  
0                1          0     SW  
1                2          0     DO  
2                3          0     DO  
3                4          0     DO  
4                5          0     DO  
..             ...        ...    ...  
657            658          0     NS  
658            659          0     NS  
659            660          0     NS  
660            661          0     NS  
661            662          0     CX  

[3014 rows x 18 columns]

In [21]:
vehicle_only_assignments = pd.DataFrame(vehicle_only_assignments)

In [22]:
vehicle_only_assignments['modelFile'] = 'veroviz/models/ub_truck.gltf'

In [23]:
vehicle_only_assignments

odID objectID                     modelFile  startLat  startLon  \
0          1   Boston  veroviz/models/ub_truck.gltf  42.13989 -71.49430   
1          2   Boston  veroviz/models/ub_truck.gltf  42.14031 -71.49422   
2          3   Boston  veroviz/models/ub_truck.gltf  42.14044 -71.49443   
3          4   Boston  veroviz/models/ub_truck.gltf  42.14053 -71.49434   
4          5   Boston  veroviz/models/ub_truck.gltf  42.14059 -71.49429   
...      ...      ...                           ...       ...       ...   
15063  15064   Austin  veroviz/models/ub_truck.gltf  30.44447 -97.71011   
15064  15065   Austin  veroviz/models/ub_truck.gltf  30.44494 -97.70987   
15065  15066   Austin  veroviz/models/ub_truck.gltf  30.44510 -97.70977   
15066  15067   Austin  veroviz/models/ub_truck.gltf  30.44518 -97.70972   
15067  15068   Austin  veroviz/models/ub_truck.gltf  30.44533 -97.70963   

         endLat    endLon  startElevMeters  endElevMeters  startAltMeters  \
0      42.14031 -71.49422                0              0               0   
1      42.14044 -71.49443                0              0               0   
2      42.14053 -71.49434                0              0               0   
3      42.14059 -71.49429                0              0               0   
4      42.14072 -71.49417                0              0               0   
...         ...       ...              ...            ...             ...   
15063  30.44494 -97.70987                0              0               0   
15064  30.44510 -97.70977                0              0               0   
15065  30.44518 -97.70972                0              0               0   
15066  30.44533 -97.70963                0              0               0   
15067  30.44523 -97.70942                0              0               0   

       ...  leafletOpacity  leafletCurveType  leafletCurvature arcCurveType  \
0      ...             0.8          straight                 0     straight   
1      ...             0.8          straight                 0     straight   
2      ...             0.8          straight                 0     straight   
3      ...             0.8          straight                 0     straight   
4      ...             0.8          straight                 0     straight   
...    ...             ...               ...               ...          ...   
15063  ...             0.8          straight                 0     straight   
15064  ...             0.8          straight                 0     straight   
15065  ...             0.8          straight                 0     straight   
15066  ...             0.8          straight                 0     straight   
15067  ...             0.8          straight                 0     straight   

       useArrows cesiumColor  cesiumWeight cesiumStyle  cesiumOpacity  \
0           True      yellow             5       solid            0.8   
1           True      yellow             5       solid            0.8   
2           True      yellow             5       solid            0.8   
3           True      yellow             5       solid            0.8   
4           True      yellow             5       solid            0.8   
...          ...         ...           ...         ...            ...   
15063       True         red             5       solid            0.8   
15064       True         red             5       solid            0.8   
15065       True         red             5       solid            0.8   
15066       True         red             5       solid            0.8   
15067       True         red             5       solid            0.8   

                          popupText  
0        Route segment 1 for Boston  
1        Route segment 2 for Boston  
2        Route segment 3 for Boston  
3        Route segment 4 for Boston  
4        Route segment 5 for Boston  
...                             ...  
15063  Route segment 501 for Austin  
15064  Route segment 502 for Austin  
15065  Route s

In [24]:
vehicle_only_assignments['startTimeSec']

0        24930.400000
1        24911.573888
2        24892.747776
3        24873.921664
4        24855.095552
             ...     
15063    22253.103960
15064    22256.343168
15065    22259.582376
15066    22262.821584
15067    22266.060792
Name: startTimeSec, Length: 15068, dtype: float64

In [25]:
vehicle_only_assignments['endTimeSec']

0        24911.573888
1        24892.747776
2        24873.921664
3        24855.095552
4        24836.269440
             ...     
15063    22256.343168
15064    22259.582376
15065    22262.821584
15066    22266.060792
15067    22269.300000
Name: endTimeSec, Length: 15068, dtype: float64

In [26]:
assignments = vehicle_only_assignments
assignments['modelScale'] = 100
assignments['modelMinPxSize'] = 75
assignments['ganttColor'] = 'darkgray'
assignments['wayname'] = None
assignments['waycategory'] = None
assignments['surface'] = None
assignments['waytype'] = None
assignments['steepness'] = None
assignments['tollway'] = None

In [30]:
vrv.createCesium(assignments=assignments,
                 nodes=nodes_df,
                 cesiumDir=os.getcwd()+'/Cesium-1.116',
                 problemDir='veroviz/new')

/home/max/miniconda3/envs/vrpd/lib/python3.12/site-packages/veroviz/createCesium.py:768: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  path = path.append({
/home/max/miniconda3/envs/vrpd/lib/python3.12/site-packages/veroviz/createCesium.py:768: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  path = path.append({
/home/max/miniconda3/envs/vrpd/lib/python3.12/site-packages/veroviz/createCesium.py:768: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  path = path.append({
/home/max/miniconda3/envs/vrpd/lib/python3.12/site-packages/veroviz/createCesium.py:768: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  path = path.append({
/home/max/miniconda3

Message: File selector was written to /home/max/vrpd-amazon-dataset/visual/Cesium-1.116/veroviz/new/;veroviz;new.vrv ...
Message: Configs were written to /home/max/vrpd-amazon-dataset/visual/Cesium-1.116/veroviz/new/config.js ...
Message: Nodes were written to /home/max/vrpd-amazon-dataset/visual/Cesium-1.116/veroviz/new/displayNodes.js ...
Message: Assignments (.js) were written to /home/max/vrpd-amazon-dataset/visual/Cesium-1.116/veroviz/new/displayPaths.js ...
Message: Assignments (.czml) were written to /home/max/vrpd-amazon-dataset/visual/Cesium-1.116/veroviz/new/routes.czml ...
